# Notebook for Coursera Capstone project

# week 1

In [1]:
# import libs
import numpy as np  # useful for many scientific computing in Python
import pandas as pd # primary data structure library

In [2]:
print("Hello Capstone Project Course!")

Hello Capstone Project Course!


[Watson Studio share link](https://jp-tok.dataplatform.cloud.ibm.com/analytics/notebooks/v2/1f93ac15-f21b-449c-b6da-ac9ed73e778a/view?access_token=25d992bd79bc2469e5a1a6f3ebb529d4e3e3d7fa53822dd1dae17ff79a45995c)

# week 3

In [3]:
# Setup
pd.options.display.max_rows = None
pd.options.display.max_columns = None
pd.options.display.max_colwidth = -1

## Read table from wikipedia.  The post code is contained in  the first 'Postcode' table.

In [4]:
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
dfs = pd.read_html(url, match='Postcode', header=0)
postcode=dfs[0]
#print(type(postcode))
#print(postcode.shape)
postcode.head()

Postcode           Borough     Neighbourhood
0  M1A      Not assigned      Not assigned    
1  M2A      Not assigned      Not assigned    
2  M3A      North York        Parkwoods       
3  M4A      North York        Victoria Village
4  M5A      Downtown Toronto  Harbourfront

## Remove Not Assigned Boroughs

In [5]:
# remove Not assigned
postcode_edit=postcode[postcode['Borough']!='Not assigned']
postcode_edit.head()

Postcode           Borough     Neighbourhood
2  M3A      North York        Parkwoods       
3  M4A      North York        Victoria Village
4  M5A      Downtown Toronto  Harbourfront    
5  M5A      Downtown Toronto  Regent Park     
6  M6A      North York        Lawrence Heights

## Replace NA Neighbourhoods with its Borough

In [6]:
# set Borough for Not assigned Neighbourhood
idx=postcode_edit['Neighbourhood']=='Not assigned'
postcode_edit.loc[idx, 'Neighbourhood']=postcode_edit.loc[idx, 'Borough']
#postcode_edit.set_index('Postcode').reset_index()
postcode_edit[idx]

/opt/conda/envs/Python36/lib/python3.6/site-packages/pandas/core/indexing.py:190: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  self._setitem_with_indexer(indexer, value)
/opt/conda/envs/Python36/lib/python3.6/site-packages/ipykernel/__main__.py:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  app.launch_new_instance()


Postcode       Borough Neighbourhood
8  M7A      Queen's Park  Queen's Park

## group and join same postcode and Borough

In [7]:
pcdata = postcode_edit.groupby(['Postcode', 'Borough'], sort=False)['Neighbourhood'].apply(lambda x: ','.join(x.astype(str))).reset_index()
pcdata.head()

Postcode           Borough                    Neighbourhood
0  M3A      North York        Parkwoods                      
1  M4A      North York        Victoria Village               
2  M5A      Downtown Toronto  Harbourfront,Regent Park       
3  M6A      North York        Lawrence Heights,Lawrence Manor
4  M7A      Queen's Park      Queen's Park

## Shape of final dataframe

In [8]:
pcdata.shape

(103, 3)

# week3-part2

## setup geocoder

In [9]:
!pip install geocoder
import geocoder # import geocoder

     |████████████████████████████████| 102kB 13.7MB/s ta 0:00:01


## Define util function for geocoder

In [10]:
def findlonlat_geocoder(postal_code):
    # initialize your variable to None
    lat_lng_coords = None
    
    # loop until you get the coordinates
    while(lat_lng_coords is None):
        #g = geocoder.google('{}, Toronto, Ontario'.format(postal_code)) # ACCESS_DENIED; probably require access token
        # this seem to reliably work, Thanks to Joana Smith - https://www.coursera.org/learn/applied-data-science-capstone/profiles/08f0dfd5c661ddf3f9a548157003dff4
        g = geocoder.arcgis('{}, Toronto, Ontario'.format(postal_code))
        print('{}:{}'.format(postal_code, g.latlng))
        lat_lng_coords = g.latlng

    latitude = lat_lng_coords[0]
    longitude = lat_lng_coords[1]
    
    return(latitude, longitude)

### test

In [11]:
findlonlat_geocoder('M5G')

M5G:[43.65609081300005, -79.38492999999994]


(43.65609081300005, -79.38492999999994)

## Add lonlat of each postal code

In [12]:
data = pcdata['Postcode'].apply(lambda x: pd.Series(findlonlat_geocoder(x)))
data.columns=['Latitude', 'Longitude']
data.head()

M3A:[43.752440000000036, -79.32927072599995]
M4A:[43.730420577000075, -79.31331999999998]
M5A:[43.65512000000007, -79.36263979699999]
M6A:[43.72312500000004, -79.45158914699994]
M7A:[43.66110229800006, -79.39103499999999]
M9A:[43.662242201000026, -79.52837877199994]
M1B:[43.811525000000074, -79.19551721399995]
M3B:[43.74919500000004, -79.36190541699995]
M4B:[43.707535000000064, -79.31177329699995]
M5B:[43.65736301100003, -79.37817999999999]
M6B:[43.70799000000005, -79.44836733199998]
M9B:[43.64969222700006, -79.55394499999994]
M1C:[43.78573000000006, -79.15874999999994]
M3C:[43.72142500000007, -79.34345278999996]
M4C:[43.68966500000005, -79.30716910999996]
M5C:[43.65121000000005, -79.37548057699996]
M6C:[43.692105179000066, -79.43035499999996]
M9C:[43.648573449000025, -79.57824999999997]
M1E:[43.76569000000006, -79.17525603599995]
M4E:[43.67684518300007, -79.29522499999996]
M5E:[43.64516015600003, -79.37367499999993]
M6E:[43.68864000000008, -79.45101525299998]
M1G:[43.76835912100006, -

Latitude  Longitude
0  43.752440 -79.329271
1  43.730421 -79.313320
2  43.655120 -79.362640
3  43.723125 -79.451589
4  43.661102 -79.391035

## concat geocode

In [27]:
pcdata_new=pd.concat([pcdata, data], axis=1)
pcdata_new

Postcode           Borough  \
0    M3A      North York         
1    M4A      North York         
2    M5A      Downtown Toronto   
3    M6A      North York         
4    M7A      Queen's Park       
5    M9A      Etobicoke          
6    M1B      Scarborough        
7    M3B      North York         
8    M4B      East York          
9    M5B      Downtown Toronto   
10   M6B      North York         
11   M9B      Etobicoke          
12   M1C      Scarborough        
13   M3C      North York         
14   M4C      East York          
15   M5C      Downtown Toronto   
16   M6C      York               
17   M9C      Etobicoke          
18   M1E      Scarborough        
19   M4E      East Toronto       
20   M5E      Downtown Toronto   
21   M6E      York               
22   M1G      Scarborough        
23   M4G      East York          
24   M5G      Downtown Toronto   
25   M6G      Downtown Toronto   
26   M1H      Scarborough        
27   M2H      North York         
28   M3H      North York         
29   M4H      East York          
30   M5H      Downtown Toronto   
31   M6H      West Toronto       
32   M1J      Scarborough        
33   M2J      North York         
34   M3J      North York         
35   M4J      East York          
36   M5J      Downtown Toronto   
37   M6J      West Toronto       
38   M1K      Scarborough        
39   M2K      North York         
40   M3K      North York         
41   M4K      East Toronto       
42   M5K      Downtown Toronto   
43   M6K      West Toronto       
44   M1L      Scarborough        
45   M2L      North York         
46   M3L      North York         
47   M4L      East Toronto       
48   M5L      Downtown Toronto   
49   M6L      North York         
50   M9L      North York         
51   M1M      Scarborough        
52   M2M      North York         
53   M3M      North York         
54   M4M      East Toronto       
55   M5M      North York         
56   M6M      York               
57   M9M      North York         
58   M1N      Scarborough        
59   M2N      North York         
60   M3N      North York         
61   M4N      Central Toronto    
62   M5N      Central Toronto    
63   M6N      York               
64   M9N      York               
65   M1P      Scarborough        
66   M2P      North York         
67   M4P      Central Toronto    
68   M5P      Central Toronto    
69   M6P      West Toronto       
70   M9P      Etobicoke          
71   M1R      Scarborough        
72   M2R      North York         
73   M4R      Central Toronto    
74   M5R      Central Toronto    
75   M6R      West Toronto       
76   M7R      Mississauga        
77   M9R      Etobicoke          
78   M1S      Scarborough        
79   M4S      Central Toronto    
80   M5S      Downtown Toronto   
81   M6S      West Toronto       
82   M1T      Scarborough        
83   M4T      Central Toronto    
84   M5T      Downtown Toronto   
85   M1V      Scarborough        
86   M4V      Central Toronto    
87   M5V      Downtown Toronto   
88   M8V      Etobicoke          
89   M9V      Etobicoke          
90   M1W      Scarborough        
91   M4W      Downtown Toronto   
92   M5W      Downtown Toronto   
93   M8W      Etobicoke          
94   M9W      Etobicoke          
95   M1X      Scarborough        
96   M4X      Downtown Toronto   
97   M5X      Downtown Toronto   
98   M8X      Etobicoke          
99   M4Y      Downtown Toronto   
100  M7Y      East Toronto       
101  M8Y      Etobicoke          
102  M8Z      Etobicoke          

                                                                                                                       Neighbourhood  \
0    Parkwoods                                                                                                                         
1    Victoria Village                                                                                                                  
2    Harbourfront,Regent Park                              

# week3-3
For this assignment, I will analyze commonalities of venues in the postal code areas in Boroughs containing 'Toronto'.   The basic analysis flow is same as provided in the Coursera "Applied Data Science" course week3 Lab https://www.coursera.org/learn/applied-data-science-capstone/home/welcome.

## import libs

In [37]:
import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

## Package Plan ##

  environment location: /opt/conda/envs/Python36

  added / updated specs: 
    - geopy


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    ca-certificates-2019.9.11  |       hecc5488_0         144 KB  conda-forge
    certifi-2019.9.11          |           py36_0         147 KB  conda-forge
    geopy-1.20.0               |             py_0          57 KB  conda-forge
    openssl-1.1.1c             |       h516909a_0         2.1 MB  conda-forge
    geographiclib-1.50         |             py_0          34 KB  conda-forge
    ------------------------------------------------------------
                                           Total:         2.5 MB

The following NEW packages will be INSTALLED:

    geographiclib:   1.50-py_0         conda-forge
    geopy:           1.20.0-py_0       conda-forge

The following packages will be UPDATED:

    ca-

## create dataframe with Boroughs containing Toronto

In [31]:
pcdata_toronto=pcdata_new[pcdata_new['Borough'].str.contains('Toronto')]
print(pcdata_toronto.shape)
pcdata_toronto.head()

(38, 5)


Postcode           Borough             Neighbourhood   Latitude  Longitude
2   M5A      Downtown Toronto  Harbourfront,Regent Park  43.655120 -79.362640
9   M5B      Downtown Toronto  Ryerson,Garden District   43.657363 -79.378180
15  M5C      Downtown Toronto  St. James Town            43.651210 -79.375481
19  M4E      East Toronto      The Beaches               43.676845 -79.295225
20  M5E      Downtown Toronto  Berczy Park               43.645160 -79.373675

## Define utility to gather venues

In [33]:
# The code was removed by Watson Studio for sharing.

Your credentails:
CLIENT_ID: SFOI1LSHZYPN20MQJFSHU3FVJRWXXC3ZOURGWSLLNO24OYWO
CLIENT_SECRET:GNL5N5NYVCDKI3OSZBZLCFCWB41GO2BSZWJSN2CDWRTSXSJJ


In [131]:
# These method definitions were provided in the Coursera "Applied Data Science" course week3 Lab
#  https://www.coursera.org/learn/applied-data-science-capstone/home/welcome

def getNearbyVenues(names, latitudes, longitudes, radius=500, LIMIT=100):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])
        
        #for v in results:
        #   n=v['venue']['categories'][0]['name']
        #    if 'Neigh' in n:
        #        print('{} in {}'.format(n, name))

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighbourhood', 
                  'Neighbourhood Latitude', 
                  'Neighbourhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
        
    return(nearby_venues)

# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

## Get nearby venues for each Neighbourhood

In [142]:
toronto_venues = getNearbyVenues(names=pcdata_toronto['Neighbourhood'],
                                   latitudes=pcdata_toronto['Latitude'],
                                   longitudes=pcdata_toronto['Longitude']
                                  )

Harbourfront,Regent Park
Ryerson,Garden District
St. James Town
The Beaches
Berczy Park
Central Bay Street
Christie
Adelaide,King,Richmond
Dovercourt Village,Dufferin
Harbourfront East,Toronto Islands,Union Station
Little Portugal,Trinity
The Danforth West,Riverdale
Design Exchange,Toronto Dominion Centre
Brockton,Exhibition Place,Parkdale Village
The Beaches West,India Bazaar
Commerce Court,Victoria Hotel
Studio District
Lawrence Park
Roselawn
Davisville North
Forest Hill North,Forest Hill West
High Park,The Junction South
North Toronto West
The Annex,North Midtown,Yorkville
Parkdale,Roncesvalles
Davisville
Harbord,University of Toronto
Runnymede,Swansea
Moore Park,Summerhill East
Chinatown,Grange Park,Kensington Market
Deer Park,Forest Hill SE,Rathnelly,South Hill,Summerhill West
CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara
Rosedale
Stn A PO Boxes 25 The Esplanade
Cabbagetown,St. James Town
First Canadian Place,Underground city


In [143]:
print(toronto_venues.shape)
toronto_venues.head()
#toronto_venues.loc[toronto_venues['Venue Category']=='Neighborhood']

(1748, 7)


Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0  Harbourfront,Regent Park  43.65512               -79.36264                  
1  Harbourfront,Regent Park  43.65512               -79.36264                  
2  Harbourfront,Regent Park  43.65512               -79.36264                  
3  Harbourfront,Regent Park  43.65512               -79.36264                  
4  Harbourfront,Regent Park  43.65512               -79.36264                  

                    Venue  Venue Latitude  Venue Longitude      Venue Category  
0  Roselle Desserts        43.653447      -79.362017        Bakery              
1  Tandem Coffee           43.653559      -79.361809        Coffee Shop         
2  Figs Breakfast & Lunch  43.655675      -79.364503        Breakfast Spot      
3  Body Blitz Spa East     43.654735      -79.359874        Spa                 
4  Cocina Economica        43.654959      -79.365657        Mexican Restaurant

## Analyze Neighbourhood

In [144]:
toronto_venues.groupby('Neighbourhood').count()

Neighbourhood Latitude  \
Neighbourhood                                                                                                                  
Adelaide,King,Richmond                                                                                100                      
Berczy Park                                                                                           64                       
Brockton,Exhibition Place,Parkdale Village                                                            67                       
Business Reply Mail Processing Centre 969 Eastern                                                     100                      
CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara  67                       
Cabbagetown,St. James Town                                                                            39                       
Central Bay Street                                                                                    97                       
Chinatown,Grange Park,Kensington Market                                                               95                       
Christie                                                                                              10                       
Church and Wellesley                                                                                  86                       
Commerce Court,Victoria Hotel                                                                         100                      
Davisville                                                                                            26                       
Davisville North                                                                                      6                        
Deer Park,Forest Hill SE,Rathnelly,South Hill,Summerhill West                                         7                        
Design Exchange,Toronto Dominion Centre                                                               100                      
Dovercourt Village,Dufferin                                                                           16                       
First Canadian Place,Underground city                                                                 100                      
Forest Hill North,Forest Hill West                                                                    2                        
Harbord,University of Toronto                                                                         54                       
Harbourfront East,Toronto Islands,Union Station                                                       4                        
Harbourfront,Regent Park                                                                              23                       
High Park,The Junction South                                                                          3                        
Lawrence Park                                                                                         2                        
Little Portugal,Trinity                                                                               61                       
Moore Park,Summerhill East                                                                            5                        
North Toronto West                                                                                    4                        
Parkdale,Roncesvalles                                                                                 53                       
Rosedale                                                                                              4                        
Roselawn                                                                                              1                        
Runnymede,Swansea                                                                                     40                       
Ryerso

In [145]:
print('There are {} uniques categories.'.format(len(toronto_venues['Venue Category'].unique())))

There are 210 uniques categories.


In [146]:
# one hot encoding
toronto_onehot = pd.get_dummies(toronto_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
toronto_onehot['Neighbourhood'] = toronto_venues['Neighbourhood'] 

# move neighborhood column to the first column
fixed_columns = [toronto_onehot.columns[-1]] + list(toronto_onehot.columns[:-1])
toronto_onehot = toronto_onehot[fixed_columns]

toronto_onehot.head()

Neighbourhood  Afghan Restaurant  American Restaurant  \
0  Harbourfront,Regent Park  0                  0                     
1  Harbourfront,Regent Park  0                  0                     
2  Harbourfront,Regent Park  0                  0                     
3  Harbourfront,Regent Park  0                  0                     
4  Harbourfront,Regent Park  0                  0                     

   Antique Shop  Art Gallery  Art Museum  Arts & Crafts Store  \
0  0             0            0           0                     
1  0             0            0           0                     
2  0             0            0           0                     
3  0             0            0           0                     
4  0             0            0           0                     

   Asian Restaurant  Athletics & Sports  BBQ Joint  Baby Store  Bagel Shop  \
0  0                 0                   0          0           0            
1  0                 0                   0          0           0            
2  0                 0                   0          0           0            
3  0                 0                   0          0           0            
4  0                 0                   0          0           0            

   Bakery  Bank  Bar  Basketball Stadium  Beer Bar  Beer Store  \
0  1       0     0    0                   0         0            
1  0       0     0    0                   0         0            
2  0       0     0    0                   0         0            
3  0       0     0    0                   0         0            
4  0       0     0    0                   0         0            

   Belgian Restaurant  Bike Shop  Bistro  Board Shop  Bookstore  Boutique  \
0  0                   0          0       0           0          0          
1  0                   0          0       0           0          0          
2  0                   0          0       0           0          0          
3  0                   0          0       0           0          0          
4  0                   0          0       0           0          0          

   Brazilian Restaurant  Breakfast Spot  Brewery  Bubble Tea Shop  Building  \
0  0                     0               0        0                0          
1  0                     0               0        0                0          
2  0                     1               0        0                0          
3  0                     0               0        0                0          
4  0                     0               0        0                0          

   Burger Joint  Burrito Place  Bus Line  Bus Stop  Butcher  Café  \
0  0             0              0         0         0        0      
1  0             0              0         0         0        0      
2  0             0              0         0         0        0      
3  0             0              0         0         0        0      
4  0             0              0         0         0        0      

   Camera Store  Caribbean Restaurant  Cheese Shop  Chinese Restaurant  \
0  0             0                     0            0                    
1  0             0                     0            0                    
2  0             0                     0            0                    
3  0             0                     0            0                    
4  0             0                     0            0                    

   Church  Clothing Store  Cocktail Bar  Coffee Shop  College Arts Building  \
0  0       0               0             0            0                       
1  0       0               0             1            0                       
2  0       0               0             0            0                       
3  0       0               0             0            0                       
4  0       0               0             0            0                       

   College Gym  College Rec Center  Colombian Restaurant 

In [195]:
toronto_grouped = toronto_onehot.groupby('Neighbourhood').mean().reset_index()
print(toronto_grouped.shape)
toronto_grouped.head()

(38, 211)


Neighbourhood  \
0  Adelaide,King,Richmond                                                                                 
1  Berczy Park                                                                                            
2  Brockton,Exhibition Place,Parkdale Village                                                             
3  Business Reply Mail Processing Centre 969 Eastern                                                      
4  CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara   

   Afghan Restaurant  American Restaurant  Antique Shop  Art Gallery  \
0  0.0                0.03                 0.0           0.010000      
1  0.0                0.00                 0.0           0.015625      
2  0.0                0.00                 0.0           0.014925      
3  0.0                0.03                 0.0           0.000000      
4  0.0                0.00                 0.0           0.000000      

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0  0.0         0.000000             0.030000          0.0                  
1  0.0         0.000000             0.000000          0.0                  
2  0.0         0.014925             0.000000          0.0                  
3  0.0         0.000000             0.020000          0.0                  
4  0.0         0.000000             0.014925          0.0                  

   BBQ Joint  Baby Store  Bagel Shop    Bakery  Bank       Bar  \
0  0.000000   0.0         0.000000    0.020000  0.0   0.030000   
1  0.015625   0.0         0.015625    0.031250  0.0   0.000000   
2  0.000000   0.0         0.000000    0.044776  0.0   0.029851   
3  0.000000   0.0         0.000000    0.010000  0.0   0.040000   
4  0.000000   0.0         0.000000    0.029851  0.0   0.044776   

   Basketball Stadium  Beer Bar  Beer Store  Belgian Restaurant  Bike Shop  \
0  0.000000            0.010000  0.0         0.000000            0.000000    
1  0.015625            0.031250  0.0         0.015625            0.000000    
2  0.000000            0.029851  0.0         0.000000            0.000000    
3  0.000000            0.000000  0.0         0.000000            0.000000    
4  0.000000            0.014925  0.0         0.000000            0.014925    

     Bistro  Board Shop  Bookstore  Boutique  Brazilian Restaurant  \
0  0.000000  0.0         0.02       0.0       0.01                   
1  0.015625  0.0         0.00       0.0       0.00                   
2  0.000000  0.0         0.00       0.0       0.00                   
3  0.000000  0.0         0.00       0.0       0.01                   
4  0.000000  0.0         0.00       0.0       0.00                   

   Breakfast Spot   Brewery  Bubble Tea Shop  Building  Burger Joint  \
0  0.020000        0.000000  0.0              0.01      0.030000       
1  0.031250        0.000000  0.0              0.00      0.000000       
2  0.014925        0.000000  0.0              0.00      0.014925       
3  0.010000        0.000000  0.0              0.00      0.010000       
4  0.000000        0.014925  0.0              0.00      0.000000       

   Burrito Place  Bus Line  Bus Stop  Butcher      Café  Camera Store  \
0  0.01           0.0       0.000000  0.0      0.060000  0.0            
1  0.00           0.0       0.000000  0.0      0.031250  0.0            
2  0.00           0.0       0.014925  0.0      0.059701  0.0            
3  0.02           0.0       0.000000  0.0      0.050000  0.0            
4  0.00           0.0       0.000000  0.0      0.044776  0.0            

   Caribbean Restaurant  Cheese Shop  Chinese Restaurant  Church  \
0  0.000000              0.00000      0.0                 0.0      
1  0.000000              0.03125      0.0                 0.0      
2  0.014925              0.00000      0.0                 0.0      
3  0.000000              0.00000      0.0                 0.0      
4  0.014925              0.00000      0.0                 

## Top 5 frequent venues per Neighbourhood

In [196]:
num_top_venues = 5

# T is same as dataframe.transpose()

for hood in toronto_grouped['Neighbourhood']:
    print("----"+hood+"----")
    temp = toronto_grouped[toronto_grouped['Neighbourhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----Adelaide,King,Richmond----
          venue  freq
0  Coffee Shop   0.09
1  Café          0.06
2  Hotel         0.04
3  Restaurant    0.03
4  Burger Joint  0.03


----Berczy Park----
            venue  freq
0  Coffee Shop     0.08
1  Restaurant      0.05
2  Cocktail Bar    0.05
3  Farmers Market  0.03
4  Lounge          0.03


----Brockton,Exhibition Place,Parkdale Village----
            venue  freq
0  Coffee Shop     0.10
1  Café            0.06
2  Bakery          0.04
3  Sandwich Place  0.04
4  Restaurant      0.04


----Business Reply Mail Processing Centre 969 Eastern----
         venue  freq
0  Coffee Shop  0.09
1  Café         0.05
2  Steakhouse   0.04
3  Hotel        0.04
4  Bar          0.04


----CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara----
                venue  freq
0  Coffee Shop         0.10
1  Italian Restaurant  0.07
2  Bar                 0.04
3  Café                0.04
4  Restaurant          0.04


----Cab

## Top 5 frequent venues in Toronto

In [232]:
toronto_grouped.drop(columns='Neighbourhood').sum().to_frame('freqsum').sort_values('freqsum', ascending=False).reset_index().rename(columns={'index':'Venue Category'}).head()

Venue Category   freqsum
0  Coffee Shop              2.558045
1  Park                     2.241163
2  Café                     1.822913
3  Health & Beauty Service  1.142857
4  Restaurant               1.111297

**Observation** - Seems Toronto has a lot of Cafes and Parks.  Seems a great neighbourhood to live in.

### Define utility functions and create top 10 venues dataframe to prepare for clustering
These are copied from the Lab.

In [233]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

In [278]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighbourhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighbourhood'] = toronto_grouped['Neighbourhood']

for ind in np.arange(toronto_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(toronto_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighbourhood  \
0  Adelaide,King,Richmond                                                                                 
1  Berczy Park                                                                                            
2  Brockton,Exhibition Place,Parkdale Village                                                             
3  Business Reply Mail Processing Centre 969 Eastern                                                      
4  CN Tower,Bathurst Quay,Island airport,Harbourfront West,King and Spadina,Railway Lands,South Niagara   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0  Coffee Shop           Café                  Hotel                  
1  Coffee Shop           Restaurant            Cocktail Bar           
2  Coffee Shop           Café                  Sandwich Place         
3  Coffee Shop           Café                  Bar                    
4  Coffee Shop           Italian Restaurant    Bar                    

  4th Most Common Venue 5th Most Common Venue   6th Most Common Venue  \
0  Gastropub             American Restaurant   Restaurant               
1  Seafood Restaurant    Bakery                Café                     
2  Restaurant            Bakery                Furniture / Home Store   
3  Hotel                 Steakhouse            American Restaurant      
4  Café                  Restaurant            Bakery                   

  7th Most Common Venue          8th Most Common Venue 9th Most Common Venue  \
0  Burger Joint          Gym                            Bar                    
1  Hotel                 Breakfast Spot                 Italian Restaurant     
2  Pub                   Vegetarian / Vegan Restaurant  Beer Bar               
3  Restaurant            Italian Restaurant             Sushi Restaurant       
4  Sandwich Place        Speakeasy                      Gym / Fitness Center   

  10th Most Common Venue  
0  Asian Restaurant       
1  Cheese Shop            
2  Supermarket            
3  Pizza Place            
4  Pub

### Cluster neighbourhoods

In [279]:
# set number of clusters
kclusters = 5

toronto_grouped_clustering = toronto_grouped.drop('Neighbourhood', 1)

toronto_grouped_clustering

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(toronto_grouped_clustering)

# check cluster labels generated for each row in the dataframe
# 38 is the number of Venue Categories (checked using shape above)
kmeans.labels_[0:38]

array([4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 4, 0, 4, 4, 4, 4, 0, 4, 3, 4, 0,
       2, 4, 0, 0, 4, 0, 1, 4, 4, 4, 4, 4, 4, 4, 4, 0], dtype=int32)

In [280]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)

toronto_merged = toronto_venues

# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
toronto_merged = toronto_merged.join(neighborhoods_venues_sorted.set_index('Neighbourhood'), on='Neighbourhood')

toronto_merged.head(100) # check the last columns!

Neighbourhood  Neighbourhood Latitude  Neighbourhood Longitude  \
0   Harbourfront,Regent Park  43.655120              -79.36264                  
1   Harbourfront,Regent Park  43.655120              -79.36264                  
2   Harbourfront,Regent Park  43.655120              -79.36264                  
3   Harbourfront,Regent Park  43.655120              -79.36264                  
4   Harbourfront,Regent Park  43.655120              -79.36264                  
5   Harbourfront,Regent Park  43.655120              -79.36264                  
6   Harbourfront,Regent Park  43.655120              -79.36264                  
7   Harbourfront,Regent Park  43.655120              -79.36264                  
8   Harbourfront,Regent Park  43.655120              -79.36264                  
9   Harbourfront,Regent Park  43.655120              -79.36264                  
10  Harbourfront,Regent Park  43.655120              -79.36264                  
11  Harbourfront,Regent Park  43.655120              -79.36264                  
12  Harbourfront,Regent Park  43.655120              -79.36264                  
13  Harbourfront,Regent Park  43.655120              -79.36264                  
14  Harbourfront,Regent Park  43.655120              -79.36264                  
15  Harbourfront,Regent Park  43.655120              -79.36264                  
16  Harbourfront,Regent Park  43.655120              -79.36264                  
17  Harbourfront,Regent Park  43.655120              -79.36264                  
18  Harbourfront,Regent Park  43.655120              -79.36264                  
19  Harbourfront,Regent Park  43.655120              -79.36264                  
20  Harbourfront,Regent Park  43.655120              -79.36264                  
21  Harbourfront,Regent Park  43.655120              -79.36264                  
22  Harbourfront,Regent Park  43.655120              -79.36264                  
23  Ryerson,Garden District   43.657363              -79.37818                  
24  Ryerson,Garden District   43.657363              -79.37818                  
25  Ryerson,Garden District   43.657363              -79.37818                  
26  Ryerson,Garden District   43.657363              -79.37818                  
27  Ryerson,Garden District   43.657363              -79.37818                  
28  Ryerson,Garden District   43.657363              -79.37818                  
29  Ryerson,Garden District   43.657363              -79.37818                  
30  Ryerson,Garden District   43.657363              -79.37818                  
31  Ryerson,Garden District   43.657363              -79.37818                  
32  Ryerson,Garden District   43.657363              -79.37818                  
33  Ryerson,Garden District   43.657363              -79.37818                  
34  Ryerson,Garden District   43.657363              -79.37818                  
35  Ryerson,Garden District   43.657363              -79.37818                  
36  Ryerson,Garden District   43.657363              -79.37818                  
37  Ryerson,Garden District   43.657363              -79.37818                  
38  Ryerson,Garden District   43.657363              -79.37818                  
39  Ryerson,Garden District   43.657363              -79.37818                  
40  Ryerson,Garden District   43.657363              -79.37818                  
41  Ryerson,Garden District   43.657363              -79.37818                  
42  Ryerson,Garden District   43.657363              -79.37818                  
43  Ryerson,Garden District   43.657363              -79.37818                  
44  Ryerson,Garden District   43.657363              -79.37818                  
45  Ryerson,Garden District   43.657363              -79.37818                  
46  Ryerson,Garden District   43.657363              -79.37818                  
47  Ryerson,Garden District   43.657363              -79.37818                  
48  Ryerson,Garden District   43.657363       

### Visualize cluster

#### Get location of Toronto

In [282]:
address = 'Toronto, Canada'

geolocator = Nominatim(user_agent="toronto_explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of Toronto are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of Toronto are 43.653963, -79.387207.


#### visualize

In [287]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(toronto_merged['Neighbourhood Latitude'], toronto_merged['Neighbourhood Longitude'], toronto_merged['Neighbourhood'], toronto_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

#### Examine clusters

##### Cluster 1

In [289]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 0, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood Latitude  Venue Longitude     Venue Category  \
580   43.683262              -79.355989        Discount Store      
581   43.683262              -79.356588        Park                
582   43.683262              -79.355078        Bus Line            
583   43.683262              -79.356461        Grocery Store       
928   43.712815              -79.387776        Park                
929   43.712815              -79.391557        Breakfast Spot      
930   43.712815              -79.392881        Food & Drink Shop   
931   43.712815              -79.393873        Clothing Store      
932   43.712815              -79.390880        Hotel               
933   43.712815              -79.393537        Gym                 
934   43.694785              -79.413965        Lawyer              
935   43.694785              -79.413900        Park                
936   43.659975              -79.463038        Park                
937   43.659975              -79.466628        Convenience Store   
938   43.659975              -79.462190        Sandwich Place      
939   43.714523              -79.404255        Park                
940   43.714523              -79.411970        Playground          
941   43.714523              -79.405786        Gym Pool            
942   43.714523              -79.411978        Garden              
1145  43.690655              -79.387781        Gym                 
1146  43.690655              -79.384504        Restaurant          
1147  43.690655              -79.382900        Tennis Court        
1148  43.690655              -79.383465        Playground          
1149  43.690655              -79.386506        Convenience Store   
1319  43.681940              -79.376549        Bank                
1320  43.681940              -79.378934        Playground          
1321  43.681940              -79.373788        Park                
1322  43.681940              -79.380091        Building            

      Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
580   0               Park                  Bus Line               
581   0               Park                  Bus Line               
582   0               Park                  Bus Line               
583   0               Park                  Bus Line               
928   0               Food & Drink Shop     Clothing Store         
929   0               Food & Drink Shop     Clothing Store         
930   0               Food & Drink Shop     Clothing Store         
931   0               Food & Drink Shop     Clothing Store         
932   0               Food & Drink Shop     Clothing Store         
933   0               Food & Drink Shop     Clothing Store         
934   0               Park                  Lawyer                 
935   0               Park                  Lawyer                 
936   0               Park                  Convenience Store      
937   0               Park                  Convenience Store      
938   0               Park                  Convenience Store      
939   0               Park                  Playground             
940   0               Park                  Playground             
941   0               Park                  Playground             
942   0               Park                  Playground             
1145  0               Convenience Store     Playground             
1146  0               Convenience Store     Playground             
1147  0               Convenience Store     Playground             
1148  0               Convenience Store     Playground             
1149  0               Convenience Store     Playground             
1319  0               Park                  Playground             
1320  0               Park                  Playground             
1321  0               Park                  Playground             
1322  0               Park                  Playground             

     3rd Most Common Venue 4th Most Common Venue 5th Most Co

###### Observation
This cluster seems to be where people live or work, since there are parks/playground, convenience store and shops.

##### Cluster 2

In [291]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 1, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood Latitude  Venue Longitude           Venue Category  \
927  43.711941              -79.41581         Health & Beauty Service   

     Cluster Labels    1st Most Common Venue 2nd Most Common Venue  \
927  1               Health & Beauty Service  Yoga Studio            

    3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
927  Electronics Store     Flea Market           Fish Market            

    6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
927  Fish & Chips Shop     Fast Food Restaurant  Farmers Market         

    9th Most Common Venue 10th Most Common Venue  
927  Farm                  Falafel Restaurant

###### Observation
This cluster does not have enough samples to observe from.  Perhaps we need to reduce size of cluster.

##### Cluster 3

In [294]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 2, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood Latitude  Venue Longitude Venue Category  Cluster Labels  \
925  43.72816               -79.382860        Swim School    2                
926  43.72816               -79.382805        Bus Line       2                

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
925  Bus Line              Swim School           Yoga Studio            
926  Bus Line              Swim School           Yoga Studio            

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
925  Elementary School     Flea Market           Fish Market            
926  Elementary School     Flea Market           Fish Market            

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
925  Fish & Chips Shop     Fast Food Restaurant  Farmers Market         
926  Fish & Chips Shop     Fast Food Restaurant  Farmers Market         

    10th Most Common Venue  
925  Farm                   
926  Farm

###### Observation
This cluster seems to indicate where the schools are located.

##### Cluster 4

In [296]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 3, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood Latitude  Venue Longitude   Venue Category  Cluster Labels  \
515  43.62347               -79.391107        Music Venue      3                
516  43.62347               -79.386945        Harbor / Marina  3                
517  43.62347               -79.390266        Harbor / Marina  3                
518  43.62347               -79.391311        Café             3                

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
515  Harbor / Marina       Music Venue           Café                   
516  Harbor / Marina       Music Venue           Café                   
517  Harbor / Marina       Music Venue           Café                   
518  Harbor / Marina       Music Venue           Café                   

           4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
515  Eastern European Restaurant  Fish Market           Fish & Chips Shop      
516  Eastern European Restaurant  Fish Market           Fish & Chips Shop      
517  Eastern European Restaurant  Fish Market           Fish & Chips Shop      
518  Eastern European Restaurant  Fish Market           Fish & Chips Shop      

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
515  Fast Food Restaurant  Farmers Market        Farm                   
516  Fast Food Restaurant  Farmers Market        Farm                   
517  Fast Food Restaurant  Farmers Market        Farm                   
518  Fast Food Restaurant  Farmers Market        Farm                   

    10th Most Common Venue  
515  Falafel Restaurant     
516  Falafel Restaurant     
517  Falafel Restaurant     
518  Falafel Restaurant

###### Observation
This cluster is where people or tourist seem to gather to enjoy (Music, Cafe, food).

##### Cluster 5

In [298]:
toronto_merged.loc[toronto_merged['Cluster Labels'] == 4, toronto_merged.columns[[1] + list(range(5, toronto_merged.shape[1]))]]

Neighbourhood Latitude  Venue Longitude  \
0     43.655120              -79.362017         
1     43.655120              -79.361809         
2     43.655120              -79.364503         
3     43.655120              -79.359874         
4     43.655120              -79.365657         
5     43.655120              -79.364955         
6     43.655120              -79.361149         
7     43.655120              -79.365609         
8     43.655120              -79.365873         
9     43.655120              -79.359515         
10    43.655120              -79.358967         
11    43.655120              -79.366355         
12    43.655120              -79.364917         
13    43.655120              -79.357947         
14    43.655120              -79.365681         
15    43.655120              -79.356980         
16    43.655120              -79.364753         
17    43.655120              -79.359725         
18    43.655120              -79.365583         
19    43.655120              -79.359667         
20    43.655120              -79.358970         
21    43.655120              -79.358917         
22    43.655120              -79.357119         
23    43.657363              -79.376073         
24    43.657363              -79.380015         
25    43.657363              -79.378343         
26    43.657363              -79.380641         
27    43.657363              -79.377586         
28    43.657363              -79.380495         
29    43.657363              -79.381403         
30    43.657363              -79.381167         
31    43.657363              -79.379768         
32    43.657363              -79.379199         
33    43.657363              -79.379276         
34    43.657363              -79.376968         
35    43.657363              -79.374110         
36    43.657363              -79.381620         
37    43.657363              -79.381385         
38    43.657363              -79.381306         
39    43.657363              -79.381949         
40    43.657363              -79.380390         
41    43.657363              -79.381726         
42    43.657363              -79.378891         
43    43.657363              -79.378880         
44    43.657363              -79.380856         
45    43.657363              -79.379200         
46    43.657363              -79.380413         
47    43.657363              -79.380512         
48    43.657363              -79.378315         
49    43.657363              -79.380966         
50    43.657363              -79.380567         
51    43.657363              -79.376643         
52    43.657363              -79.381015         
53    43.657363              -79.382177         
54    43.657363              -79.381878         
55    43.657363              -79.378507         
56    43.657363              -79.379460         
57    43.657363              -79.382586         
58    43.657363              -79.374221         
59    43.657363              -79.380889         
60    43.657363              -79.383524         
61    43.657363              -79.379296         
62    43.657363              -79.383684         
63    43.657363              -79.380910         
64    43.657363              -79.380822         
65    43.657363              -79.380120         
66    43.657363              -79.380400         
67    43.657363              -79.380696         
68    43.657363              -79.381661         
69    43.657363              -79.380248         
70    43.657363              -79.382891         
71    43.657363              -79.381929         
72    43.657363              -79.380740         
73    43.657363              -79.382462         
74    43.657363              -79.383284         
75    43.657363              -79.383621         
76    43.657363              -79.382949         
77    43.657363              -79.380245         
78    43.657363              -79.380974         
79    43.657363              -79.383761         
80    43.657363              -79.3792

###### Observation
This cluster highlights breakfast and bakery...  Maybe office area?

### Summary for week3-3
Clustering neighourhood containing Toronto shows there are a lot of coffee shops (cafes) in the area, and seem an enjoying location.
We probably should look into all the postal codes to seek more findings (since we filtered to Neighbourhoods containing 'Toronto' only, for sake of the assignment).

#### Future study
- Analyze entire data (instead of just 'Toronto')
- Adjust cluster num
- Reserach where we can retrieve Toronto geocode?
- Use it and Folium coropleth to highligh postal code area - https://towardsdatascience.com/visualizing-data-at-the-zip-code-level-with-folium-d07ac983db20
